### Q1. Getting the embeddings model

In [1]:
#pip install sentence_transformers==2.7.0
from sentence_transformers import SentenceTransformer
embedding_model = SentenceTransformer('multi-qa-distilbert-cos-v1')

/opt/conda/envs/llm-course/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
user_question = "I just discovered the course. Can I still join it?"

In [3]:
user_question_emb = embedding_model.encode(user_question).tolist()
user_question_emb[0]

0.07822265475988388

In [4]:
import requests 

base_url = 'https://github.com/DataTalksClub/llm-zoomcamp/blob/main'
relative_url = '03-vector-search/eval/documents-with-ids.json'
docs_url = f'{base_url}/{relative_url}?raw=1'
docs_response = requests.get(docs_url)
documents = docs_response.json()

In [5]:
documents


[{'text': "The purpose of this document is to capture frequently asked technical questions\nThe exact day and hour of the course will be 15th Jan 2024 at 17h00. The course will start with the first  “Office Hours'' live.1\nSubscribe to course public Google Calendar (it works from Desktop only).\nRegister before the course starts using this link.\nJoin the course Telegram channel with announcements.\nDon’t forget to register in DataTalks.Club's Slack and join the channel.",
  'section': 'General course-related questions',
  'question': 'Course - When will the course start?',
  'course': 'data-engineering-zoomcamp',
  'id': 'c02e79ef'},
 {'text': 'GitHub - DataTalksClub data-engineering-zoomcamp#prerequisites',
  'section': 'General course-related questions',
  'question': 'Course - What are the prerequisites for this course?',
  'course': 'data-engineering-zoomcamp',
  'id': '1f6520ca'},
 {'text': "Yes, even if you don't register, you're still eligible to submit the homeworks.\nBe aware

In [6]:
ml_document = [item for item in documents if item.get('course') == 'machine-learning-zoomcamp']

In [7]:
len(ml_document)

375

### Q2. Creating the embeddings

In [8]:
import numpy as np
from tqdm.auto import tqdm

In [9]:
embeddings = []

for doc in tqdm(ml_document):
    qt_text = f"{doc['question']} {doc['text']}"
    doc['qt_vector'] = embedding_model.encode(qt_text)
    embedding = embedding_model.encode(qt_text)
    embeddings.append(embedding) 





100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 375/375 [02:06<00:00,  2.96it/s]


In [10]:
ml_document

[{'text': 'Machine Learning Zoomcamp FAQ\nThe purpose of this document is to capture frequently asked technical questions.\nWe did this for our data engineering course and it worked quite well. Check this document for inspiration on how to structure your questions and answers:\nData Engineering Zoomcamp FAQ\nIn the course GitHub repository there’s a link. Here it is: https://airtable.com/shryxwLd0COOEaqXo\nwork',
  'section': 'General course-related questions',
  'question': 'How do I sign up?',
  'course': 'machine-learning-zoomcamp',
  'id': '0227b872',
  'qt_vector': array([ 8.80590528e-02,  1.55935483e-02,  7.92558193e-02,  2.52757873e-02,
          7.55765066e-02, -3.90596949e-02, -4.13813852e-02,  2.52918135e-02,
          2.43241284e-02,  3.62585997e-03, -7.28285545e-03, -3.28751542e-02,
          6.12956472e-02, -5.71101010e-02,  1.16774784e-02, -1.79442130e-02,
          4.49206047e-02, -5.41605875e-02, -1.92261033e-03,  1.48329930e-02,
          7.91360065e-03, -3.43127362e-0

In [11]:
X = np.array(embeddings)

In [12]:
X.shape

(375, 768)


### Q3. Search

In [13]:
v = embedding_model.encode(user_question)

In [14]:
scores = X.dot(v)

In [15]:
print(scores)

[ 2.89217263e-01  4.35050726e-01  2.20572561e-01  1.28085926e-01
  3.28754455e-01  4.58999664e-01  4.48930591e-01  2.70170599e-01
  2.13975310e-01  3.39745760e-01  1.63339168e-01  3.15918088e-01
  1.53621323e-02  4.14240420e-01  6.50657296e-01  4.12786484e-01
  2.02390462e-01  4.71707582e-01  3.74821007e-01  3.53319108e-01
  4.50558245e-01  1.85430944e-01  3.45526993e-01  8.22948217e-02
 -2.19077598e-02 -4.64250743e-02  8.60690773e-02  9.87197682e-02
 -2.14188285e-02  1.28751006e-02  2.54870541e-02  3.66866291e-02
  4.56338078e-02 -2.05279887e-02  1.82662532e-02  3.39789167e-02
  1.66510604e-03  1.03209512e-02  3.40170749e-02 -2.65231431e-02
 -4.11909968e-02 -4.97983992e-02 -6.20346665e-02 -7.63561390e-03
  4.61616889e-02  6.95944112e-03  4.77613509e-02 -9.97766852e-04
 -5.60126789e-02 -5.96206151e-02  2.05209196e-01 -1.16968602e-01
 -2.34160442e-02 -1.52456751e-02 -6.83515333e-03 -8.61715078e-02
  2.02636905e-02 -2.51591802e-02  4.21313569e-04 -3.79212126e-02
 -3.21442187e-02  2.48612

In [16]:
np.max(scores)

0.6506573

In [17]:
class VectorSearchEngine():
    def __init__(self, documents, embeddings):
        self.documents = documents
        self.embeddings = embeddings

    def search(self, v_query, num_results=10):
        scores = self.embeddings.dot(v_query)
        idx = np.argsort(-scores)[:num_results]
        return [self.documents[i] for i in idx]

search_engine = VectorSearchEngine(documents=ml_document, embeddings=X)
search_engine.search(v, num_results=5)

[{'text': 'Yes, you can. You won’t be able to submit some of the homeworks, but you can still take part in the course.\nIn order to get a certificate, you need to submit 2 out of 3 course projects and review 3 peers’ Projects by the deadline. It means that if you join the course at the end of November and manage to work on two projects, you will still be eligible for a certificate.',
  'section': 'General course-related questions',
  'question': 'The course has already started. Can I still join it?',
  'course': 'machine-learning-zoomcamp',
  'id': 'ee58a693',
  'qt_vector': array([ 8.06286409e-02, -6.66388795e-02,  2.52730623e-02, -1.30044082e-02,
          7.58728236e-02, -5.94627075e-02, -2.18838379e-02,  2.90004001e-03,
          7.92835199e-04, -5.22241509e-03, -3.36517990e-02, -2.79135145e-02,
          5.81165552e-02,  3.97483334e-02,  5.44185564e-02, -3.82517129e-02,
          6.30573705e-02, -3.89698781e-02,  4.33594891e-04, -3.55845094e-02,
          1.75642478e-03,  2.570036

### Q4. Hit-rate for our search engine

In [18]:
# Let's evaluate the performance of our own search engine. We will use the hitrate metric for evaluation.
# First, load the ground truth dataset:
import pandas as pd

base_url = 'https://github.com/DataTalksClub/llm-zoomcamp/blob/main'
relative_url = '03-vector-search/eval/ground-truth-data.csv'
ground_truth_url = f'{base_url}/{relative_url}?raw=1'

df_ground_truth = pd.read_csv(ground_truth_url)
df_ground_truth = df_ground_truth[df_ground_truth.course == 'machine-learning-zoomcamp']
ground_truth = df_ground_truth.to_dict(orient='records')

In [ ]:
ground_truth

In [20]:
def question_vector(question):
    v_q = embedding_model.encode(question)
    return search_engine.search(v_q, num_results=5)
        

In [55]:
relevance_total = []

for q in tqdm(ground_truth):
        doc_id = q['document']
        results = question_vector(q['question'])
        relevance = [d['id'] == doc_id for d in results]
        relevance_total.append(relevance)




100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1830/1830 [01:24<00:00, 21.67it/s]


In [22]:
def hit_rate(relevance_total):
    cnt = 0

    for line in relevance_total:
        if True in line:
            cnt = cnt + 1

    return cnt / len(relevance_total)

In [56]:
hit_rate(relevance_total)

0.9398907103825137

### Q5. Indexing with Elasticsearch

In [24]:
from elasticsearch import Elasticsearch

  
es_client = Elasticsearch(hosts=["http://localhost:9200"], request_timeout=30)

In [25]:
index_settings = {
    "settings": {
        "number_of_shards": 1,
        "number_of_replicas": 0
    },
    "mappings": {
        "properties": {
            "text": {"type": "text"},
            "section": {"type": "text"},
            "question": {"type": "text"},
            "course": {"type": "keyword"},
            "id": {"type": "keyword"},
            "qt_vector": {
                "type": "dense_vector",
                "dims": 768,
                "index": True,
                "similarity": "cosine"
            },
        }
    }
}

index_name = "course-questions"

es_client.indices.delete(index=index_name, ignore_unavailable=True)
es_client.indices.create(index=index_name, body=index_settings)



ObjectApiResponse({'acknowledged': True, 'shards_acknowledged': True, 'index': 'course-questions'})

In [26]:
for doc in tqdm(ml_document):
    es_client.index(index=index_name, document=doc)

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 375/375 [00:09<00:00, 40.29it/s]


In [64]:
def elastic_search_knn(field, vector):
    
    knn_query = {
    "field": 'qt_vector',
    "query_vector": vector,
    "k": 5,
    "num_candidates": 10000
    }

    search_query = {
        "knn": knn_query,
        "_source": ["text", "section", "question", "course", "id"]
    }

    es_results = es_client.search(
        index=index_name,
        body=search_query
    )
    
    result_docs = []
        
    for hit in es_results['hits']['hits']:
        result_docs.append(hit['_source'])


    return result_docs

In [65]:
def question_text_vector_knn(question):
    v_q = embedding_model.encode(question)
    return elastic_search_knn('qt_vector', v_q)

In [66]:
question_text_vector_knn(user_question)

[{'question': 'The course has already started. Can I still join it?',
  'course': 'machine-learning-zoomcamp',
  'section': 'General course-related questions',
  'text': 'Yes, you can. You won’t be able to submit some of the homeworks, but you can still take part in the course.\nIn order to get a certificate, you need to submit 2 out of 3 course projects and review 3 peers’ Projects by the deadline. It means that if you join the course at the end of November and manage to work on two projects, you will still be eligible for a certificate.',
  'id': 'ee58a693'},
 {'question': 'I just joined. What should I do next? How can I access course materials?',
  'course': 'machine-learning-zoomcamp',
  'section': 'General course-related questions',
  'text': 'Welcome to the course! Go to the course page (http://mlzoomcamp.com/), scroll down and start going through the course materials. Then read everything in the cohort folder for your cohort’s year.\nClick on the links and start watching the vid

Highest score id: ee58a693

In [67]:
relevance_total = []

for q in tqdm(ground_truth):
    doc_id = q['document']
    results = question_text_vector_knn(q['question'])
    relevance = [d['id'] == doc_id for d in results]
    relevance_total.append(relevance)

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1830/1830 [01:20<00:00, 22.69it/s]


### Q6. Hit-rate for Elasticsearch

In [68]:
hit_rate(relevance_total)

0.9398907103825137